Ce notebook à pour objectif de faire une première analyse des données avec de l'extraction d'information et de la classification à partir du dataset qui a été pré-traiter. Ce même dataset, contient des informations sur les films issus du scrapping de alocine et de leur commentaire

In [45]:
%pip install scikit-learn xgboost catboost lightgbm scikit-optimize

Note: you may need to restart the kernel to use updated packages.


In [60]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt 
import seaborn as sns
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error
from sklearn.preprocessing import StandardScaler
from xgboost import XGBRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import KFold
import plotly.express as px
import plotly.graph_objects as go
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import OneHotEncoder, LabelEncoder
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.model_selection import train_test_split, cross_val_score
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, AdaBoostClassifier
from xgboost import XGBClassifier
from catboost import CatBoostClassifier
from lightgbm import LGBMClassifier
from skopt import BayesSearchCV
from skopt.space import Real, Integer, Categorical
from sklearn.metrics import accuracy_score, log_loss
import warnings
import logging

In [61]:
# Désactiver les avertissements
warnings.filterwarnings("ignore")

# Désactiver les logs des bibliothèques comme LightGBM, XGBoost, etc.
logging.getLogger("lightgbm").setLevel(logging.CRITICAL)
logging.getLogger("xgboost").setLevel(logging.CRITICAL)
logging.getLogger("sklearn").setLevel(logging.CRITICAL)

# Désactiver complètement tous les logs si nécessaire
logging.disable(logging.CRITICAL)

LOAD DATA

In [47]:
data = pd.read_excel('../dataset/Main_dataset.xlsx')
data.head()

id_film                                                url  \
0   236613  https://www.allocine.fr//film/fichefilm_gen_cf...   
1   264525  https://www.allocine.fr//film/fichefilm_gen_cf...   
2   236613  https://www.allocine.fr//film/fichefilm_gen_cf...   
3   271453  https://www.allocine.fr//film/fichefilm_gen_cf...   
4   279217  https://www.allocine.fr//film/fichefilm_gen_cf...   

                  titre                                           synopsis  \
0                 Mulan  Lorsque l’Empereur de Chine publie un décret s...   
1  Sons of Philadelphia  Philadelphie. Il y a trente ans, la famille de...   
2                 Mulan  Lorsque l’Empereur de Chine publie un décret s...   
3            L'Etreinte  Margaux a perdu son mari et commence une nouve...   
4        No Sudden Move  Detroit, au milieu des années 1950. Des crimin...   

              public note_presse nb_notes_presse nb_critiques_presse  \
0        Tout public         2.6              16                  16   
1  Interdit - 12 ans         3.4              24                  24   
2        Tout public         2.6              16                  16   
3        Tout public         3.3              22                  22   
4        Tout public           4               5                   5   

   note_spectateurs  nb_notes_spectateurs  ...        realisateur     id  \
0               2.6                  8000  ...          Niki Caro   1213   
1               2.5                  1478  ...       Jérémie Guez   5029   
2               2.6                  8000  ...          Niki Caro   1234   
3               2.4                   531  ...    Ludovic Bergery  10483   
4               2.9                   484  ...  Steven Soderbergh   2722   

           auteur  note                                            contenu  \
0   Cinéphiles 44   4.0  “Mulan” est le remake en prises de vues réelle...   
1       lionelb30   2.0  Déjà vu et mieux traité. Cette histoire de riv...   
2  Gilles Boudier   0.5  Un navet ! Une série Z ! Pas de bande son, dia...   
3    Elisabeth G.   1.5  Un film gris et décevant que porte tant bien q...   
4       Hotinhere   3.0  Porté par un casting séduisant, un polar diver...   

  likes dislikes                                  tag       scenariste  \
0    14        9                              Evasion    Amanda Silver   
1     5        1                  Adaptation de roman     Jérémie Guez   
2     6        9               Sabre - épée et katana       Rick Jaffa   
3     8        1  Période de la vie : la cinquantaine  Ludovic Bergery   
4     1        0                              Détroit       Ed Solomon   

         date  
0  30-11-2020  
1  26-05-2021  
2  30-11-2020  
3  19-05-2021  
4   8-09-2021  

[5 rows x 32 columns]

Rappel des informations principale sur le dataset

In [48]:
print("Dataset shape: ", data.shape)

Dataset shape:  (100000, 32)


Notre algorithme de classification de film n'allant pas prendre en compte les film n'ayant pas de notation, il est donc important de les pré-filtré

In [49]:
data = data.replace("Inconnu", np.nan).dropna()
print("Data shape après processing : ",data.shape)
data

Data shape après processing :  (51971, 32)


/var/folders/9x/gl7s8kd16p7d9v5lgt59hqg40000gn/T/ipykernel_46594/1292281669.py:1: FutureWarning:

Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`



id_film                                                url  \
3       271453  https://www.allocine.fr//film/fichefilm_gen_cf...   
5       275050  https://www.allocine.fr//film/fichefilm_gen_cf...   
8       172048  https://www.allocine.fr//film/fichefilm_gen_cf...   
12      274530  https://www.allocine.fr//film/fichefilm_gen_cf...   
14      270443  https://www.allocine.fr//film/fichefilm_gen_cf...   
...        ...                                                ...   
99989   251303  https://www.allocine.fr//film/fichefilm_gen_cf...   
99995   277532  https://www.allocine.fr//film/fichefilm_gen_cf...   
99996   281251  https://www.allocine.fr//film/fichefilm_gen_cf...   
99997   237864  https://www.allocine.fr//film/fichefilm_gen_cf...   
99999   272249  https://www.allocine.fr//film/fichefilm_gen_cf...   

                                 titre  \
3                           L'Etreinte   
5                                Drunk   
8                    Bad Boys For Life   
12                            Bac Nord   
14                                Miss   
...                                ...   
99989  Les Trolls 2 - Tournée mondiale   
99995             Tout Simplement Noir   
99996            Le Braquage du siècle   
99997             Les Nouveaux mutants   
99999                     Petite soeur   

                                                synopsis             public  \
3      Margaux a perdu son mari et commence une nouve...        Tout public   
5      Quatre amis décident de mettre en pratique la ...        Tout public   
8      Les Bad Boys Mike Lowrey et Marcus Burnett se ...        Tout public   
12     2012. Les quartiers Nord de Marseille détienne...        Tout public   
14     Alex, petit garçon gracieux de 9 ans qui navig...        Tout public   
...                                                  ...                ...   
99989  Reine Barb, membre de la royauté hard-rock, ai...        Tout public   
99995  JP, un acteur raté de 40 ans, décide d’organis...        Tout public   
99996  Argentine, 2006. Un groupe de cambrioleurs s’a...        Tout public   
99997  Rahne Sinclair, Illyana Rasputin, Sam Guthrie ...  Interdit - 12 ans   
99999  Lisa est une dramaturge allemande qui a abando...        Tout public   

       note_presse  nb_notes_presse  nb_critiques_presse  note_spectateurs  \
3              3.3             22.0                 22.0               2.4   
5              3.9             39.0                 39.0               4.1   
8              2.4             24.0                 24.0               3.2   
12             3.5             34.0                 34.0               4.2   
14             3.4             25.0                 25.0               3.5   
...            ...              ...                  ...               ...   
99989          2.8             12.0                 12.0               2.5   
99995          3.8             32.0                 32.0               2.8   
99996          3.4             16.0                 16.0               3.8   
99997          2.3             11.0                 11.0               2.1   
99999          3.4             14.0                 14.0               3.2   

       nb_notes_spectateurs  ...        realisateur     id            auteur  \
3                       531  ...    Ludovic Bergery  10483      Elisabeth G.   
5                     12883  ...  Thomas Vinterberg    508  gimliamideselfes   
8                     12607  ...       Adil El Arbi    653          Julien V   
12                    22093  ...     Cédric Jimenez    331       Manu Frakes   
14                     3200  ...        Ruben Alves   3524         lionelb30   
...                     ...  ...                ...    ...               ...   
99989                  2690  ...     David P. Smith   2937          Audrey L   
99995                  9051  ...           John Wax   1071           pliscal   
99996                   182  ...     Ariel Winograd   5457      Chr

In [50]:
import pandas as pd

# Supposons que 'data' soit déjà défini comme un DataFrame
analyse_colonnes = {}
for columns in data.columns:
    nbre_valeurs_null = data[columns].isnull().sum()
    nb_value_count = data[columns].value_counts().count()
    type_colonne = data[columns].dtype
    
    # Initialiser les variables
    moyenne_column = None
    median_column = None
    ecart_type = None
    
    if data[columns].dtype != object:
        moyenne_column = data[columns].mean()
        median_column = data[columns].median()
        ecart_type = data[columns].std()
    
    
    
    analyse_colonnes[columns] = [nbre_valeurs_null, nb_value_count, type_colonne, moyenne_column, median_column, ecart_type]

analyse_colonnes = pd.DataFrame.from_dict(analyse_colonnes, orient='index', columns=['nbre_valeurs_null', 'nb_value_count', 'type_colonne', 'moyenne_column', 'median_column', 'ecart_type'])
analyse_colonnes

nbre_valeurs_null  nb_value_count type_colonne  \
id_film                                   0             173        int64   
url                                       0             173       object   
titre                                     0             173       object   
synopsis                                  0             168       object   
public                                    0               5       object   
note_presse                               0              28      float64   
nb_notes_presse                           0              38      float64   
nb_critiques_presse                       0              38      float64   
note_spectateurs                          0              28      float64   
nb_notes_spectateurs                      0             165        int64   
nb_critiques_spectateurs                  0             122        int64   
duree                                     0              57      float64   
distributeur                              0              56       object   
recompenses                               0              10        int64   
type                                      0               1       object   
box_office_france                         0             172      float64   
langues                                   0              25       object   
couleur                                   0               3       object   
nationalite                               0              25       object   
categorie                                 0              20       object   
acteur                                    0            1173       object   
role                                      0            1132       object   
realisateur                               0             184       object   
id                                        0            4442        int64   
auteur                                    0            1688       object   
note                                      0              10      float64   
contenu                                   0            4440       object   
likes                                     0              66        int64   
dislikes                                  0              39        int64   
tag                                       0             538       object   
scenariste                                0             400       object   
date                                      0              88       object   

                          moyenne_column  median_column     ecart_type  
id_film                    259447.902600       269514.0   31279.329291  
url                                  NaN            NaN            NaN  
titre                                NaN            NaN            NaN  
synopsis                             NaN            NaN            NaN  
public                               NaN            NaN            NaN  
note_presse                     3.060805            3.1       0.572688  
nb_notes_presse                17.502261           16.0       8.614280  
nb_critiques_presse            17.502261           16.0       8.614280  
note_spectateurs                3.017912            3.1       0.660808  
nb_notes_spectateurs         3555.612553         2379.0    4101.496992  
nb_critiques_spectateurs      207.661831          116.0     241.233571  
duree                         102.206750           97.0      14.075079  
distributeur                         NaN            NaN            NaN  
recompenses                     0.658252            0.0       1.623353  
type                                 NaN            NaN            NaN  
box_office_france          644404.363991       223953.0  967851.197302  
langues                              NaN            NaN            NaN  
couleur                              NaN            NaN            NaN  
nationalite                          NaN            NaN            NaN  
categorie                            NaN            NaN  

Labelisaton de mes films

Avec une note median de 3.1 pour les spectateur et pour la presse


On va s'intéresser ici sur est ce qu'il filme va être intéressant ou non en fonction des notes qu'il a reçu. Pour cela, on va considérer que les films ayant une note supérieur à 3.6 sont intéressants et les autres non intéressants. On va donc créer une nouvelle colonne qui va contenir cette information.

Faison une analyse statistique sur les films afin de choisir notre bonne labelisation (partons du principe que le top 15% sont des bon films, le dernier tier sont des mauvais film et que le reste est moyen)

In [132]:
# Creation d'un hist des notes
fig1 = px.histogram(data, x='note_presse', nbins=20, title="Répartition des notes de la presse")
fig2 = px.histogram(data, x='note_spectateurs', nbins=20, title="Répartition des notes des spectateurs")
fig3 = px.histogram(data, x='note', nbins=20, title="Répartition des notes par commentaire")
fig1.show()
fig2.show()
fig3.show()

In [140]:
q1_note_spec = data['note_spectateurs'].quantile(0.333)
q3_note_spec = data['note_spectateurs'].quantile(0.85)
iqr_note_spec = q3_note_spec - q1_note_spec
print("IQR note spectateurs : ", iqr_note_spec)
q1_note_presse = data['note_presse'].quantile(0.333)
q3_note_presse = data['note_presse'].quantile(0.85)
iqr_note_presse = q3_note_presse - q1_note_presse
print("IQR note presse : ", iqr_note_presse)
q1_note_commentaire = data['note'].quantile(0.333)
q3_note_commentaire = data['note'].quantile(0.86)
iqr_note_commentaire = q3_note_commentaire - q1_note_commentaire
print("IQR note commentaire : ", iqr_note_commentaire)

print("Valeur Q1 Press : ", q1_note_presse)
print("Valeur Q3 Press : ", q3_note_presse)
print("Valeur Q1 Spectateurs : ", q1_note_spec)
print("Valeur Q3 Spectateurs : ", q3_note_spec)
print("Valeur Q1 Notes global : ", q1_note_commentaire)
print("Valeur Q3 Notes globals : ", q3_note_commentaire)

IQR note spectateurs :  1.1999999999999997
IQR note presse :  0.8000000000000003
IQR note commentaire :  2.0
Valeur Q1 Press :  2.9
Valeur Q3 Press :  3.7
Valeur Q1 Spectateurs :  2.6
Valeur Q3 Spectateurs :  3.8
Valeur Q1 Notes global :  2.5
Valeur Q3 Notes globals :  4.5


Créons maintenant un cluster afin d'évaluer si oui ou non on a des groupes de films qui se dégagent

In [142]:
data["Qualité_film"] = data.apply(
    lambda x: "Mauvais Film" if float(x["note_presse"]) < q1_note_presse and float(x["note"]) < q1_note_commentaire else " Très Bon Film"
    if float(x["note_presse"]) >= q3_note_presse and float(x["note"]) >= q3_note_commentaire else "On ne sait pas", axis=1)

data["Qualité_film"].value_counts()

Qualité_film
On ne sait pas    41944
Mauvais Film       8163
 Très Bon Film     1864
Name: count, dtype: int64

In [143]:
data[data["Qualité_film"] == " Très Bon Film"].sort_values(by="note", ascending=True)["contenu"]

30635    Un régal ! Une histoire touchante mais surtout...
47645    Aller voir ce film, lundi 20 juillet 2 020, so...
26736    Kurosawa signe un superbe thriller situé dans ...
69670    Pour mettre en scène l’injustice essuyée par R...
26874    J'ai aimé ce film plein d'humanité et de poési...
                               ...                        
40574    Immersion en Normandie ; un film magnifique, d...
40398    Super film très émouvant pour tout les âges !L...
40353    Vivement une saison 2. Démon Slayer est sans d...
41399    excellent film, tant sur le dessin, l histoire...
99896    Film incroyable !!!! Il dure 2h et on décroche...
Name: contenu, Length: 1864, dtype: object

On va entrainer un modèle de classification sur les données d'entrainement afin de définir si un film est bon ou mauvais (vu que les films moyen on sait pas trop)

In [144]:
pannel_classif = data[data["Qualité_film"] != "On ne sait pas"]
X = pannel_classif.drop(columns=["Qualité_film"])
y = pannel_classif["Qualité_film"]

# Encode target labels with value between 0 and n_classes-1
label_encoder = LabelEncoder()
y_encoded = label_encoder.fit_transform(y)
y_encoded

array([1, 1, 0, ..., 1, 1, 1])

On fait une classification bassé sur un training set de 80% et un test set de 20% avec de stratification afin de garder la même répartition des classes

In [145]:
# Séparation des données en train et test
X_train, X_test, y_train, y_test = train_test_split(X, y_encoded, test_size=0.2, random_state=42,stratify=y_encoded)
print(X_train.describe())

             id_film  note_presse  nb_notes_presse  nb_critiques_presse  \
count    8021.000000  8021.000000      8021.000000          8021.000000   
mean   244984.793667     2.637576        14.941404            14.941404   
std     34796.383170     0.653124         8.890652             8.890652   
min     42303.000000     1.500000         3.000000             3.000000   
25%    237864.000000     2.300000        10.000000            10.000000   
50%    251303.000000     2.400000        12.000000            12.000000   
75%    271607.000000     2.800000        19.000000            19.000000   
max    295759.000000     4.400000        43.000000            43.000000   

       note_spectateurs  nb_notes_spectateurs  nb_critiques_spectateurs  \
count       8021.000000           8021.000000               8021.000000   
mean           2.567573           4822.801147                251.218676   
std            0.694553           4211.211765                220.634024   
min            1.300000 

In [146]:
# Identification des colonnes numériques et catégorielles
numeric_features = X.select_dtypes(include=['int64', 'float64']).columns
categorical_features = X.select_dtypes(include=['object', 'bool']).columns

# Création des transformers
numeric_transformer = Pipeline(steps=[
    ('scaler', StandardScaler())
])

categorical_transformer = Pipeline(steps=[
    ('encoder', OneHotEncoder(drop='first', handle_unknown='ignore'))
])

# ColumnTransformer pour les prétraitements
preprocessor = ColumnTransformer(
    transformers=[
        ('num', numeric_transformer, numeric_features),
        ('cat', categorical_transformer, categorical_features)
    ])

# Initialisation des modèles avec leurs espaces de recherche bayésienne
models = {
    "Random Forest": (RandomForestClassifier(), {
        'model__n_estimators': Integer(50, 500),
        'model__max_depth': Integer(3, 20),
        'model__min_samples_split': Integer(2, 20)
    }),
    "XGBoost": (XGBClassifier(use_label_encoder=False, eval_metric='logloss'), {
        'model__n_estimators': Integer(50, 500),
        'model__max_depth': Integer(3, 20),
        'model__learning_rate': Real(0.01, 0.3, prior='log-uniform')
    }),
    "Gradient Boosting": (GradientBoostingClassifier(), {
        'model__n_estimators': Integer(50, 500),
        'model__learning_rate': Real(0.01, 0.3, prior='log-uniform'),
        'model__max_depth': Integer(3, 20)
    }),
    "AdaBoost": (AdaBoostClassifier(algorithm="SAMME"), {
        'model__n_estimators': Integer(50, 500),
        'model__learning_rate': Real(0.01, 1, prior='log-uniform')
    }),
    "CatBoost": (CatBoostClassifier(verbose=0), {
        'model__iterations': Integer(50, 500),
        'model__depth': Integer(3, 10),
        'model__learning_rate': Real(0.01, 0.3, prior='log-uniform')
    }),
    "LightGBM": (LGBMClassifier(), {
    'model__n_estimators': Integer(50, 500),
    'model__learning_rate': Real(0.01, 0.3, prior='log-uniform'),
    'model__num_leaves': Integer(20, 150),
    'model__min_gain_to_split': Real(0.01, 0.1)
})
}



Afin d'optimiser la recherhce des hyperparamètres, on va utiliser une BayeSearchCV qui permet de poser un espace vectoriel et trouver par la suite la meilleur combinaison d'hyperparamètres<>

In [147]:
# Initialisation du dataset de tracking des performances
performance_tracking = []

best_models = {}

for name, (model, search_space) in models.items():
    pipeline = Pipeline(steps=[
        ('preprocessor', preprocessor),
        ('model', model)
    ])
    
    bayes_search = BayesSearchCV(
        pipeline,
        search_spaces=search_space,
        n_iter=30,  # Nombre d'itérations pour la recherche bayésienne
        cv=3,
        scoring='accuracy',
        n_jobs=-1,
        random_state=42
    )
    
    bayes_search.fit(X_train, y_train)
    best_models[name] = bayes_search.best_estimator_
    
    # Évaluation
    y_pred = best_models[name].predict(X_test)
    acc = accuracy_score(y_test, y_pred)
    loss = log_loss(y_test, best_models[name].predict_proba(X_test))
    
    print(f"{name} Best Accuracy: {acc:.4f}")
    
    # Stocker les performances dans le dataset
    performance_tracking.append({
        "Model": name,
        "Best Accuracy": acc,
        "Training Loss": loss,
        "Predictions": y_pred.tolist()
    })

# Convertir en DataFrame pour analyse
performance_df = pd.DataFrame(performance_tracking)

# Visualisation avec Plotly
fig = px.bar(performance_df, x='Model', y='Best Accuracy', title='Comparaison des performances des modèles')
fig.show()


huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The 

Random Forest Best Accuracy: 1.0000


/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/xgboost/core.py:158: UserWarning: [15:57:56] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/xgboost/core.py:158: UserWarning: [15:57:56] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/xgboost/core.py:158: UserWarning: [15:57:56] WARNING: /Users/runner/work/xgboost/xgboost/src/learner.cc:740: 
Parameters: { "use_label_encoder" } are not used.

  warnings.warn(smsg, UserWarning)
/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:241: UserWarning: Found unknown categories in columns [10, 11, 13, 14, 15, 16] during transform. These unknown catego

XGBoost Best Accuracy: 1.0000


/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:241: UserWarning: Found unknown categories in columns [0, 1, 2, 4, 10, 11, 12, 13, 14, 15, 16] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:241: UserWarning: Found unknown categories in columns [10, 11, 13, 14, 15, 16] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:241: UserWarning: Found unknown categories in columns [10, 11, 13, 14, 15] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:241: UserWarning: Found unknown categories in columns [10, 11, 13, 14, 15, 16] durin

...

[LightGBM] [Warning] min_gain_to_split is set=0.01, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.01
[LightGBM] [Warning] min_gain_to_split is set=0.01, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.01
[LightGBM] [Warning] min_gain_to_split is set=0.01, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.01
[LightGBM] [Info] Number of positive: 4353, number of negative: 994
[LightGBM] [Warning] min_gain_to_split is set=0.01, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.01
[LightGBM] [Warning] min_gain_to_split is set=0.01, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.01
[LightGBM] [Info] Number of positive: 4353, number of negative: 994
[LightGBM] [Warning] min_gain_to_split is set=0.01, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.01
[LightGBM] [Info] Number of positive: 4354, number of negative: 994
[LightGBM] [Info] Auto-choosing row-wise

/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:241: UserWarning: Found unknown categories in columns [0, 1, 2, 4, 10, 11, 12, 13, 14, 15, 16] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:241: UserWarning: Found unknown categories in columns [10, 11, 13, 14, 15, 16] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:241: UserWarning: Found unknown categories in columns [10, 11, 13, 14, 15] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(


[LightGBM] [Warning] min_gain_to_split is set=0.1, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.1
[LightGBM] [Warning] min_gain_to_split is set=0.1, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.1
[LightGBM] [Warning] min_gain_to_split is set=0.1, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.1
[LightGBM] [Info] Number of positive: 4353, number of negative: 994
[LightGBM] [Warning] min_gain_to_split is set=0.1, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.1
[LightGBM] [Warning] min_gain_to_split is set=0.1, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.1
[LightGBM] [Info] Number of positive: 4353, number of negative: 994
[LightGBM] [Warning] min_gain_to_split is set=0.1, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.1
[LightGBM] [Info] Number of positive: 4354, number of negative: 994
[LightGBM] [Info] Auto-choosing row-wise multi-threa

/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:241: UserWarning: Found unknown categories in columns [0, 1, 2, 4, 10, 11, 12, 13, 14, 15, 16] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:241: UserWarning: Found unknown categories in columns [10, 11, 13, 14, 15] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(
/Users/henri/.pyenv/versions/3.11.6/lib/python3.11/site-packages/sklearn/preprocessing/_encoders.py:241: UserWarning: Found unknown categories in columns [10, 11, 13, 14, 15, 16] during transform. These unknown categories will be encoded as all zeros
  warnings.warn(


[LightGBM] [Warning] min_gain_to_split is set=0.07549531688595926, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.07549531688595926
[LightGBM] [Warning] min_gain_to_split is set=0.07549531688595926, min_split_gain=0.0 will be ignored. Current value: min_gain_to_split=0.07549531688595926
[LightGBM] [Info] Number of positive: 6530, number of negative: 1491
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.022394 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 2468
[LightGBM] [Info] Number of data points in the train set: 8021, number of used features: 862
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.814113 -> initscore=1.476960
[LightGBM] [Info] Start training from score 1.476960
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

Après avoir entrainer et tester notre modèle de classification nous allons faire du sentimental analysis ainsi qu'une étude plus poussé sur les données textuelles afin d'évaluer la pertinence de notre modèle de classification

Pour vérifier la pertinences de notres classification nous allons vectorisé les commentaires les plus possitif (ceux avec la meilleurs combinaison des notes de press et des notes de spectateurs) et les plus négatif (ceux avec les pires combinaisons de notes de press et de spectateurs) et les procheter sur un espace a 1024 dimensions avec TF-IDF et PCA

In [148]:
liste_meilleur_commentaire = data[(data["nb_notes_spectateurs"] > 100)].sort_values(by=["note"], ascending=False).drop_duplicates(subset=["titre"])[["contenu", "note_presse", "note_spectateurs","titre"]].head(5)
liste_meilleur_commentaire

contenu  note_presse  \
49984  J'ai adoré le film, j'ai pleuré toute ma vie m...          2.7   
49367  C'est clairement l'un de mes plus gros coup de...          3.1   
49280  Ce film nous tient en haleine tout le long ! U...          3.8   
49292  Quel magnifique biopic!L'interprétation de STR...          3.4   
10693  Merci pour cet agréable et magnifique moment. ...          2.5   

       note_spectateurs                               titre  
49984               4.2         Violet Evergarden - le film  
49367               3.8                          Summertime  
49280               4.1                         Boîte noire  
49292               3.2  Billie Holiday, une affaire d'état  
10693               3.6     J’irai mourir dans les Carpates

In [149]:
liste_meilleur_commentaire["contenu"].values

array(["J'ai adoré le film, j'ai pleuré toute ma vie mais je suis tellement déçue de la fin dans le sens qu'on a pas de nouvelles d'elle, de ( spoil )ce qui se passe après avec Gilbert etc.. je me doute qu'il n'y aura pas de suite après ce film mais pourquoi cette fin 😭 je voulais + de nouvelles d'elle !!!!",
       'C\'est clairement l\'un de mes plus gros coup de cœur du cinéma.Je voudrais le comparer à "Under the silver lake" de David Robert Mitchell mais ce n\'est pas comparable et je sais que ce dernier est sujet à controverse dans mon cercle proche et je ne voudrais pas décourager les gens de voir ce chef d\'œuvre qu\'est Summertime. Il y aura un avant et un après Summertime.Alors, je vais avoir du mal à écrire des mots pouvant expliquer l\'expérience unique que l\'on vit en voyant ce film mais je vais tenter.Premièrement le concept est incroyable, ce sont des textes écrits et joués à la perfection par les acteurs. Des textes forts et impactant accompagnés de musiques qui transce

In [150]:
liste_pire_commentaire = data[(data["nb_notes_spectateurs"] > 100)].sort_values(by=["note"], ascending=True).drop_duplicates(subset=["titre"])[["contenu", "note_presse", "note_spectateurs","titre"]].head(5)
liste_pire_commentaire

contenu  note_presse  \
29222  Une telle déception ne m'étais pas arrivée dep...          2.3   
11568  Bonjour,Honnêtement je ne sais que dire de ce ...          2.0   
36854  Si vous comparez ça à moi moche et méchant vou...          3.2   
66997  L'île Usion...... ne dure malheureusement pas ...          1.7   
36898  mais ou est la harley quinn sombre et torturee...          2.5   

       note_spectateurs                                              titre  
29222               2.1                               Les Nouveaux mutants  
11568               1.5                                         The Grudge  
36854               3.5              Les Minions 2 : Il était une fois Gru  
66997               1.8                                   Nightmare Island  
36898               2.7  Birds of Prey et la fantabuleuse histoire de H...

In [77]:
liste_meilleur_commentaire["contenu"].values

array(["Très bon film, dans la ligné des misérables.Le film est bien rythmé, les acteurs sont excellents, et les musiques bien choisies.On est vite embarqué dans l'histoire, et on vibre avec les personnages.Enfin un bon film ... français en plus, sur cette période difficile.",
       "Rare sont les films tournés au Bouthan. Splendeur  des paysages, histoire simple, au service de valeurs telles que respect de la nature, beauté de l'éducation, estime des autres. L'herbe est-elle plus belle en dehors de chez soi? Une réponse est peut-être donnée dans ce film.",
       "En ligne directe avec la série, une conclusion parfaite pour cette histoire : des moments émouvants (sans surprise !), quelques sourires, et des personnages toujours plus vivants, imparfaits et touchants, que l'on quitte sur une note d'espoir... Un moment magnifique, mâtiné de larmes, à l'image de ce qui a précédé.",
       "Nouveau film du grand Clint Eastwood, le Cas Richard Jewell est tiré des faits réels autour de l'att

Lemmentisation/ retirer les stop words de mon algorithmes

In [81]:
import nltk
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords

stop_words = set(stopwords.words('french'))

def preprocess_text(text):
    tokens = word_tokenize(str(text).lower())  # Tokenisation et mise en minuscule
    tokens = [word for word in tokens if word.isalnum()]  # Supprimer la ponctuation
    tokens = [word for word in tokens if word not in stop_words]  # Supprimer les stopwords
    return " ".join(tokens)

liste_pire_commentaire["clean_contenu"] = liste_pire_commentaire["contenu"].apply(preprocess_text)
liste_meilleur_commentaire["clean_contenu"] = liste_meilleur_commentaire["contenu"].apply(preprocess_text)


Vectorisation avec TF-IDF

On mets en place un systeme de vote de calcul de proximité afin de savoir si une phrase est bien ou pas bien

In [127]:
from sklearn.metrics.pairwise import cosine_similarity, manhattan_distances, euclidean_distances
from scipy.spatial.distance import minkowski, chebyshev, jaccard
import numpy as np

def predire_sentiment(vecteur_commentaire, threshold=0.8,vector_moyen_meilleur = None, vector_moyen_pire = None):
    """ Prend un commentaire et prédit s'il est positif ou négatif en utilisant un vote basé sur 6 distances vectorielles """

    
    # Calcul des distances pour chaque méthode
    distances = {
        "cosine": cosine_similarity([vecteur_commentaire], [vector_moyen_meilleur])[0][0] - 
                  cosine_similarity([vecteur_commentaire], [vector_moyen_pire])[0][0],

        "manhattan": - (manhattan_distances([vecteur_commentaire], [vector_moyen_meilleur])[0][0] - 
                        manhattan_distances([vecteur_commentaire], [vector_moyen_pire])[0][0]),

        "euclidean": - (euclidean_distances([vecteur_commentaire], [vector_moyen_meilleur])[0][0] - 
                        euclidean_distances([vecteur_commentaire], [vector_moyen_pire])[0][0]),

        "minkowski": - (minkowski(vecteur_commentaire, vector_moyen_meilleur, p=3) - 
                        minkowski(vecteur_commentaire, vector_moyen_pire, p=3)),

        "chebyshev": - (chebyshev(vecteur_commentaire, vector_moyen_meilleur) - 
                        chebyshev(vecteur_commentaire, vector_moyen_pire))
    }
    # Vote des distances : chaque méthode donne 1 point au sentiment dominant
    score_positif = sum(1 for d in distances.values() if d > threshold)
    score_negatif = sum(1 for d in distances.values() if d < -threshold)
    print(score_negatif)
    print(score_positif)
    # Détermination du sentiment majoritaire
    if score_positif > score_negatif:
        return "Positif"
    elif score_negatif > score_positif:
        return "Négatif"
    else:
        return "Neutre"  # Cas d'égalité (peu probable mais possible)
    
    
def predire_sentiment_tfidf(commentaire, threshold=0.8,vector_moyen_meilleur = None, vector_moyen_pire = None,vectorizer=None):
    """ Prend un commentaire et prédit s'il est positif ou négatif en utilisant un vote basé sur 6 distances vectorielles """
    if vector_moyen_pire is None or vector_moyen_meilleur is None or vectorizer is None:
        raise ValueError("Les vecteurs moyens des commentaires positifs/négatifs et le vectorizer doivent être fournis.")

    # Prétraitement du commentaire
    commentaire_prep = commentaire.lower()  # Optionnel : ajouter preprocess_text() si tu veux un nettoyage
    vecteur_commentaire = vectorizer.transform([commentaire_prep]).toarray().ravel()  # 🔥 Applatir en 1D

    # Calcul des distances pour chaque méthode
    distances = {
        "cosine": cosine_similarity([vecteur_commentaire], [vector_moyen_meilleur])[0][0] - 
                  cosine_similarity([vecteur_commentaire], [vector_moyen_pire])[0][0],

        "manhattan": - (manhattan_distances([vecteur_commentaire], [vector_moyen_meilleur])[0][0] - 
                        manhattan_distances([vecteur_commentaire], [vector_moyen_pire])[0][0]),

        "euclidean": - (euclidean_distances([vecteur_commentaire], [vector_moyen_meilleur])[0][0] - 
                        euclidean_distances([vecteur_commentaire], [vector_moyen_pire])[0][0]),

        "minkowski": - (minkowski(vecteur_commentaire, vector_moyen_meilleur, p=3) - 
                        minkowski(vecteur_commentaire, vector_moyen_pire, p=3)),

        "chebyshev": - (chebyshev(vecteur_commentaire, vector_moyen_meilleur) - 
                        chebyshev(vecteur_commentaire, vector_moyen_pire))
    }
    # Vote des distances : chaque méthode donne 1 point au sentiment dominant
    score_positif = sum(1 for d in distances.values() if d > threshold)
    score_negatif = sum(1 for d in distances.values() if d < -threshold)
    print(score_negatif)
    print(score_positif)
    # Détermination du sentiment majoritaire
    if score_positif > score_negatif:
        return "Positif"
    elif score_negatif > score_positif:
        return "Négatif"
    else:
        return "Neutre"  # Cas d'égalité (peu probable mais possible)

In [128]:
vectorizer = TfidfVectorizer(max_features=100)
X_pire = vectorizer.fit_transform(liste_pire_commentaire["clean_contenu"])
X_meilleur = vectorizer.transform(liste_meilleur_commentaire["clean_contenu"])

# Calcul du vecteur moyen pour chaque catégorie
vector_moyen_pire = np.mean(X_pire.toarray(), axis=0)
vector_moyen_meilleur = np.mean(X_meilleur.toarray(), axis=0)


test_commentaire1 = "Ce film était vraiment mauvais, une perte de temps."
print(f"Sentiment prédit : {predire_sentiment_tfidf(commentaire=test_commentaire1,vector_moyen_pire=vector_moyen_pire,vector_moyen_meilleur=vector_moyen_meilleur,vectorizer=vectorizer)}")

test_commentaire2 = "Incroyable ! L’un des meilleurs films de l’année."
print(f"Sentiment prédit : {predire_sentiment_tfidf(commentaire=test_commentaire2,vector_moyen_pire=vector_moyen_pire,vector_moyen_meilleur=vector_moyen_meilleur,vectorizer=vectorizer)}")

test_commentaire3 = "Moyen, un peu long, mais quelques bons moments."
print(f"Sentiment prédit : {predire_sentiment_tfidf(commentaire=test_commentaire3,vector_moyen_pire=vector_moyen_pire,vector_moyen_meilleur=vector_moyen_meilleur,vectorizer=vectorizer)}")

0
1
Sentiment prédit : Positif
0
1
Sentiment prédit : Positif
0
1
Sentiment prédit : Positif


Si on passe par un autre algorithme de vectorisation plus spécifique

In [129]:
from sklearn.metrics.pairwise import cosine_similarity, manhattan_distances, euclidean_distances
from scipy.spatial.distance import minkowski, chebyshev
import numpy as np
from sentence_transformers import SentenceTransformer

# Chargement du modèle SentenceTransformer
model = SentenceTransformer("paraphrase-multilingual-mpnet-base-v2")

def create_vector(commentaire):
    model = SentenceTransformer("paraphrase-multilingual-mpnet-base-v2")
    # Prétraitement du commentaire
    commentaire_prep = preprocess_text(commentaire)
    vecteur_commentaire = model.encode([commentaire_prep])
    return vecteur_commentaire.flatten()

X_pire = np.array(model.encode(liste_pire_commentaire["clean_contenu"].tolist()))
X_meilleur = np.array(model.encode(liste_meilleur_commentaire["clean_contenu"].tolist()))

# Calcul des vecteurs moyens pour chaque catégorie
vector_moyen_pire = np.mean(X_pire, axis=0)
vector_moyen_meilleur = np.mean(X_meilleur, axis=0)

test_commentaire1 = "Ce film était vraiment mauvais, une perte de temps."
print(f"Sentiment prédit : {predire_sentiment(create_vector(test_commentaire1), vector_moyen_pire=vector_moyen_pire, vector_moyen_meilleur=vector_moyen_meilleur)}")

test_commentaire2 = "Incroyable ! L’un des meilleurs films de l’année."
print(f"Sentiment prédit : {predire_sentiment(create_vector(test_commentaire2), vector_moyen_pire=vector_moyen_pire, vector_moyen_meilleur=vector_moyen_meilleur)}")

test_commentaire3 = "Moyen, un peu long, mais quelques bons moments."
print(f"Sentiment prédit : {predire_sentiment(create_vector(test_commentaire3), vector_moyen_pire=vector_moyen_pire, vector_moyen_meilleur=vector_moyen_meilleur)}")

1
0
Sentiment prédit : Négatif
0
1
Sentiment prédit : Positif
0
1
Sentiment prédit : Positif


Comme on peut voir les embeddings font beaucoup, mais finalement pourquoi un model de vectorisation multilingue est plus performant qu'un tdf-idf ?

In [131]:
print("Longueur d'un vecteur avec le multinlingue adces fr : ",len(create_vector(test_commentaire1)))
print("Longueur d'un vecteur avec tf-idf : ",vectorizer.transform(liste_meilleur_commentaire["clean_contenu"]).shape[1])

Longueur d'un vecteur avec le multinlingue adces fr :  768
Longueur d'un vecteur avec tf-idf :  100


On remarque que l'on a 7,6x plus de dimension, donc 7,6x plus précis et en prenant en compte le contexte etc... (et on ne parles même pas des openAI embeddings ou bien Mistral qui sont normé pour 1024 dimensions avec un context variable....)